In [1]:
import tensorflow as tf
print("TensorFlow version:", tf.__version__)

use_device='/gpu:0'


import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

import keras

from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Embedding, Conv1D, GlobalMaxPooling1D, Dense, Input, Concatenate, BatchNormalization
from tensorflow.keras.layers import LSTM

from tensorflow.python.client import device_lib

#import models and layers from tensorflow.keras to avoid errors like "TypeError: Checkpointable._track_checkpointable()"
from tensorflow.keras.models import Model
from tensorflow.keras.models import load_model

from tensorflow.keras.layers import Dropout, Activation, Flatten
from keras.optimizers import Adam
    
from tensorflow.keras.preprocessing import image
from tensorflow.keras.preprocessing.image import ImageDataGenerator
    
from keras.utils import layer_utils
from keras.utils.data_utils import get_file
from keras.applications.imagenet_utils import preprocess_input
from IPython.display import SVG
from keras.utils.vis_utils import model_to_dot
from keras.utils import plot_model
#import tensorflow.keras.backend as K
from keras import regularizers
    
import pickle
import pandas as pd

from datetime import datetime

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

    
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

TensorFlow version: 1.13.1


Using TensorFlow backend.


[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 16840660771792972528
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 3072013108
locality {
  bus_id: 1
  links {
  }
}
incarnation: 12954984481665642192
physical_device_desc: "device: 0, name: NVIDIA GeForce GTX 1650, pci bus id: 0000:01:00.0, compute capability: 7.5"
]


In [2]:
# define paths and functions for loading models, define names, etc
# ========================================================================================================================   
path_data= "xxx" #where is the dataset
path_data_2= "xxx" #where to store the results (specific path)



def load_model_from_path(model_path):
    """
    Load a Keras model from the specified path.
    Parameters:
        model_path (str): The path to the model file.
    Returns:
        model: The loaded Keras model.
    """
    try:
        MODEL = load_model(model_path)
        print("Model loaded successfully.")
        return MODEL
    except Exception as e:
        print("Error loading model:", e)
        
models_names_act= [
    "LogP_Acts.model",
    "Tg_Acts.model",
    "LogS_Acts.model", "pKa_Acts.model"]

In [3]:
# import chi data for testing
# ========================================================================================================================  

X1_import=path_data_2 + "SMILES_X1.txt" #where is the Xdata of the dataset (SMILES)
X2_import=path_data_2 + "SMILES_X2.txt"
# Load the saved numeric arrays from the file
Y_import=path_data_2 + "X.txt" #where is the Ydata of the dataset (property to predict)
   

# Load SMILES strings from file
with open(X1_import, 'r') as f:
    smiles_data_1 = f.readlines()
with open(X2_import, 'r') as f:
    smiles_data_2 = f.readlines()

# Load properties from file
with open(Y_import, 'r') as f:
    X_data = f.readlines()
    
print(smiles_data_1[10])
print(smiles_data_2[10])
print(X_data[10])

C=CCC

CCCCCCCC

0.31



In [4]:
# Convert the dataset into activation arrays with the pre-trained models
# ======================================================================================================================== 

# Load the tokenizer
tokenizer_path = path_data_2 + 'tokenizer_all.pkl'
with open(tokenizer_path, 'rb') as f:
    tokenizer_1 = pickle.load(f)
with open(tokenizer_path, 'rb') as f:
    tokenizer_2 = pickle.load(f) 

# Preprocess SMILES data for SMILES_1
sequences_1 = tokenizer_1.texts_to_sequences(smiles_data_1)
vocab_size_1 = len(tokenizer_1.word_index) + 1
print(f"Vocab size 1: {vocab_size_1}")
# Check the maximum index in sequences
max_index_1 = max(max(seq) for seq in sequences_1 if seq)
print(f"Maximum index in sequence 1: {max_index_1}")

# Preprocess SMILES data for SMILES_2
sequences_2 = tokenizer_2.texts_to_sequences(smiles_data_2)
vocab_size_2 = len(tokenizer_2.word_index) + 1
print(f"Vocab size 2: {vocab_size_2}")
# Check the maximum index in sequences
max_index_2 = max(max(seq) for seq in sequences_2 if seq)
print(f"Maximum index in sequence 2: {max_index_2}")

# Ensure all indices in sequences_1 are within the valid range
for seq in sequences_1:
    for idx in seq:
        if idx >= vocab_size_1:
            print(f"Found out-of-bounds index in sequences_1: {idx}")
# Ensure all indices in sequences_2 are within the valid range
for seq in sequences_2:
    for idx in seq:
        if idx >= vocab_size_2:
            print(f"Found out-of-bounds index in sequences_2: {idx}")

# ---------------------------------------------------------------------------
# Convert property data to numpy array
X_labels = np.array([float(prop.strip()) for prop in X_data])

# Define embedding dimension
embedding_dim = 128

max_len=[168, 105, 84, 88] #each model has a different padding

# logP:168, D:64, P:64, H:64, pKa:88, LogS:84, Tg:105

Vocab size 1: 32
Maximum index in sequence 1: 29
Vocab size 2: 32
Maximum index in sequence 2: 25


In [5]:
# Load each model, pass the X dataset, and store the activation arrays
# =======================================================================

acts_dict={}
for i in range(len(models_names_act)):
    model_name=models_names_act[i]
    print(model_name)
    try:
        model_path = path_data_2 + model_name
        model_temp = load_model_from_path(model_path)
        max_length = max_len[i]
        
        # Predict output 1
        padded_sequences_1 = pad_sequences(sequences_1, maxlen=max_length, padding='post')
        print("Padding ok, padding shape: ")
        print(np.shape(padded_sequences_1))
        acts_1 = model_temp.predict(padded_sequences_1)
        print("Predict ok, act shape: ")
        print(np.shape(acts_1))
        # Predict output 2
        padded_sequences_2 = pad_sequences(sequences_2, maxlen=max_length, padding='post')
        print("Padding ok, padding shape: ")
        print(np.shape(padded_sequences_2))
        acts_2 = model_temp.predict(padded_sequences_2)
        print("Predict ok, act shape: ")
        print(np.shape(acts_2))
        
        # Store activation arrays for the model
        acts_dict[model_name + "_acts_1"] = acts_1
        acts_dict[model_name + "_acts_2"] = acts_2
        
    except Exception as e:
        print("Error using model:", e)

LogP_Acts.model
Instructions for updating:
Colocations handled automatically by placer.
Model loaded successfully.
Padding ok, padding shape: 
(736, 168)
Predict ok, act shape: 
(736, 50)
Padding ok, padding shape: 
(736, 168)
Predict ok, act shape: 
(736, 50)
Tg_Acts.model
Model loaded successfully.
Padding ok, padding shape: 
(736, 105)
Predict ok, act shape: 
(736, 50)
Padding ok, padding shape: 
(736, 105)
Predict ok, act shape: 
(736, 50)
LogS_Acts.model
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
Model loaded successfully.
Padding ok, padding shape: 
(736, 84)
Predict ok, act shape: 
(736, 50)
Padding ok, padding shape: 
(736, 84)
Predict ok, act shape: 
(736, 50)
pKa_Acts.model
Model loaded successfully.
Padding ok, padding shape: 
(736, 88)
Predict ok, act shape: 
(736, 50)
Padding ok, padding shape: 
(736, 88)
Predict ok, act shape: 
(736, 50)


In [6]:
# Extract the data
X11 = acts_dict["LogP_Acts.model_acts_1"]
X12 = acts_dict["Tg_Acts.model_acts_1"]
X13 = acts_dict["LogS_Acts.model_acts_1"]
X14 = acts_dict["pKa_Acts.model_acts_1"]

# Extract the data
X21 = acts_dict["LogP_Acts.model_acts_2"]
X22 = acts_dict["Tg_Acts.model_acts_2"]
X23 = acts_dict["LogS_Acts.model_acts_2"]
X24 = acts_dict["pKa_Acts.model_acts_2"]

# Labels
y = X_labels

# Split each set of data into training and test sets
test_size = 0.8
random_state = 42


X11_train, X11_test, y_train, y_test = train_test_split(X11, y, test_size=test_size, random_state=random_state)
X12_train, X12_test = train_test_split(X12, test_size=test_size, random_state=random_state)
X13_train, X13_test = train_test_split(X13, test_size=test_size, random_state=random_state)
X14_train, X14_test = train_test_split(X14, test_size=test_size, random_state=random_state)

X21_train, X21_test = train_test_split(X21, test_size=test_size, random_state=random_state)
X22_train, X22_test = train_test_split(X22, test_size=test_size, random_state=random_state)
X23_train, X23_test = train_test_split(X23, test_size=test_size, random_state=random_state)
X24_train, X24_test = train_test_split(X24, test_size=test_size, random_state=random_state)

X_train_list = [X11_train, X12_train, X13_train, X14_train, X21_train, X22_train, X23_train, X24_train]

print(np.shape(X11_train))
print(np.shape(X21_train))
print(np.shape(X11_test))
print(np.shape(X21_test))

(147, 50)
(147, 50)
(589, 50)
(589, 50)


In [7]:
# Define the test data arrays
X_test_list = [X11_test, X12_test, X13_test, X14_test, 
               X21_test, X22_test, X23_test, X24_test]

# Save each array to a separate .npy file
for idx, array in enumerate(X_test_list):
    np.save(path_data_2 + f'X_test_{idx}.npy', array)
    
# Save y_test to a .npy file
np.save(path_data_2 + 'y_test.npy', y_test)

In [8]:
from keras.callbacks import Callback

    
# checkpoint_filepath = path_data_2 + "Weights.npy" #'checkpoint'
monitor_custom='val_mean_absolute_error' #val_mean_absolute_error   val_mean_absolute_percentage_error
mode_custom='min'

early_stop= tf.keras.callbacks.EarlyStopping(monitor=monitor_custom,  verbose=3,
                                             mode=mode_custom, patience=600, restore_best_weights=True)
# callback_list= [model_checkpoint_callback, reduce_lr, early_stop]
callback_list= [early_stop]




def Model_combined(X_train_list, y_train, alpha, NeuronsFC, lr, beta_1, beta_2, epsilon, decay, amsgrad, 
                   ep, b_s, v_s, Drop, shuffle_dataset, callback_list):
        """
    Function to create, compile and train a combined model with multiple inputs. Returns the trained Keras model.
    """
    
    # Define the neural network with 10 input branches (first 5 component 1 and the others component 2)
    size_input = 50
    N_models = 4
    input_layers = [Input(shape=(size_input,)) for _ in range(N_models*2)]
    # Normalize each input layer before concatenating
    normalized_inputs = [BatchNormalization()(input_layer) for input_layer in input_layers]
    
    merged_1 = tf.keras.layers.concatenate(normalized_inputs[:N_models])
    merged_2 = tf.keras.layers.concatenate(normalized_inputs[N_models:])
    
    # Define first network
    A = Dense(50)(merged_1)
    A = tf.keras.layers.LeakyReLU(alpha)(A)
    A = Dropout(Drop)(A)
    A = Dense(20)(A)
    A = tf.keras.layers.LeakyReLU(alpha)(A)
    A = Dropout(Drop)(A)
    # Define second network
    A2 = Dense(50)(merged_2)
    A2 = tf.keras.layers.LeakyReLU(alpha)(A2)
    A2 = Dropout(Drop)(A2)
    A2 = Dense(20)(A2)
    A2 = tf.keras.layers.LeakyReLU(alpha)(A2)
    A2 = Dropout(Drop)(A2)
    # Concatenate the outputs of the two networks
    concatenated = tf.keras.layers.concatenate([A, A2])
    merged = Dense(NeuronsFC)(concatenated)
    merged = tf.keras.layers.LeakyReLU(alpha)(merged)
    output_layer = Dense(1, activation='linear')(merged)
    
    # Create model
    MODEL = tf.keras.Model(inputs=input_layers, outputs=output_layer, name="MODEL")
    print(MODEL.summary())
    
    # Compile model
    opt = tf.keras.optimizers.Adam(lr, beta_1, beta_2, epsilon, decay, amsgrad)
    MODEL.compile(loss='mean_absolute_error', optimizer=opt,
                  metrics=['mean_absolute_error', 'mean_absolute_percentage_error'])
    
    # Train the model
    HISTORY = MODEL.fit(X_train_list, y_train, epochs=ep, batch_size=b_s, validation_split=v_s,
              shuffle=shuffle_dataset, callbacks=callback_list)
    
    return MODEL, HISTORY

In [9]:
#DATA=====================================================================================================
Mode=0
#NUMBER OF TEST===========================================================================================
number_of_test = 1
#FREEZE_LAYERS============================================================================================
is_trainable_conv1_1=True #
is_trainable_conv1_2=True #
is_trainable_conv1_3=True #
is_trainable_conv1_4=True #
is_trainable_conv1_5=True
is_trainable_HIDDEN_A1_0=True #the CNN input side of the ANN
is_trainable_HIDDEN_A2_0=True #the Hbonds input side of the ANN (1:True, 2:True, 2:False)
is_trainable_HIDDEN_FC_all=True #concatenated FCs
#HYPERPARAMETERS==========================================================================================
lr=[0.01, 0.001, 0.0001]
beta_1=0.99
beta_2=0.999
epsilon=None
decay=0
amsgrad=True
b_s=[1000, 100, 50, 20]
samples_on_control=0
samples_on_test=200
v_s= 0.2 #(samples_on_test+samples_on_control)/number_of_samples_X   
shuffle_dataset="False"
Drop_prob=0.2
alpha=0.05
reg=0.01
#WORKING PARAMETERS======================================================================================
number_epochs=5000 #
#FULLY CONNECTED=========================================================================================
NeuronsFC=50 # neurons combined FC
NeuronsFC_A2=5 #neurons in the Hbonds input
NeuronsFC_A1=5 #neurons in the CNN input
#CNN=====================================================================================================
w1=1 # must be the same if the model has been pre-trained
w2=6
w3=10
channels_1=32
channels_2=64
channels_3=128

In [10]:
# Iterate over each combination of learning rate and batch size

counter=0
Results=[]
for i in b_s:
    for j in lr:
        Name_saving="X_embedding_" + str(counter) + str(number_of_test)
        print("model name (to save): " + Name_saving)
        MODEL, HISTORY= Model_combined(X_train_list, y_train, alpha, NeuronsFC, j, beta_1, beta_2, epsilon, decay, amsgrad, 
                   number_epochs, i, v_s, Drop_prob, shuffle_dataset, callback_list)
        #save model
        try:
            MODEL.save(path_data_2 + Name_saving + ".model")
            print("Model saved")
        except:
            print("Model saved?")
            try:
                MODEL.save(path_data_2 + Name_saving + ".model")
                print("Model now saved!")
            except Exception as e:
                print("Error saving model:", e)
            
        # Extract the mean absolute error from the training history
        mean_absolute_error_model = HISTORY.history['mean_absolute_error'][-1]  # Considering the last epoch error
        val_mean_absolute_error_model = HISTORY.history['val_mean_absolute_error'][-1]
        # Append the results to the list
        Results.append([counter, j, i, mean_absolute_error_model, val_mean_absolute_error_model])            
        counter+=1

model name (to save): X_embedding_01
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 50)           0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            (None, 50)           0                                            
__________________________________________________________________________________________________
input_3 (InputLayer)            (None, 50)           0                                            
__________________________________________________________________________________________________
input_4 (InputLayer)            (None, 50)           0                                            
________________________________________________________________________

Epoch 1/5000
117/117 [==============================] - 5s 40ms/sample - loss: 1.1762 - mean_absolute_error: 1.1762 - mean_absolute_percentage_error: 261.5042 - val_loss: 1.5859 - val_mean_absolute_error: 1.5859 - val_mean_absolute_percentage_error: 1203.1013
Epoch 2/5000
117/117 [==============================] - 0s 1ms/sample - loss: 1.0833 - mean_absolute_error: 1.0833 - mean_absolute_percentage_error: 351.3838 - val_loss: 1.3082 - val_mean_absolute_error: 1.3082 - val_mean_absolute_percentage_error: 1044.3326
Epoch 3/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.7670 - mean_absolute_error: 0.7670 - mean_absolute_percentage_error: 226.4682 - val_loss: 0.9151 - val_mean_absolute_error: 0.9151 - val_mean_absolute_percentage_error: 782.7184
Epoch 4/5000
117/117 [==============================] - 0s 1ms/sample - loss: 0.5192 - mean_absolute_error: 0.5192 - mean_absolute_percentage_error: 133.8207 - val_loss: 0.7176 - val_mean_absolute_error: 0.7176 - val_mean_a

Epoch 33/5000
117/117 [==============================] - 0s 350us/sample - loss: 0.3172 - mean_absolute_error: 0.3172 - mean_absolute_percentage_error: 107.8775 - val_loss: 0.3498 - val_mean_absolute_error: 0.3498 - val_mean_absolute_percentage_error: 195.1833
Epoch 34/5000
117/117 [==============================] - 0s 316us/sample - loss: 0.3303 - mean_absolute_error: 0.3303 - mean_absolute_percentage_error: 91.1854 - val_loss: 0.3535 - val_mean_absolute_error: 0.3535 - val_mean_absolute_percentage_error: 181.8573
Epoch 35/5000
117/117 [==============================] - 0s 513us/sample - loss: 0.3313 - mean_absolute_error: 0.3313 - mean_absolute_percentage_error: 104.9504 - val_loss: 0.3591 - val_mean_absolute_error: 0.3591 - val_mean_absolute_percentage_error: 168.9520
Epoch 36/5000
117/117 [==============================] - 0s 308us/sample - loss: 0.3131 - mean_absolute_error: 0.3131 - mean_absolute_percentage_error: 91.9947 - val_loss: 0.3659 - val_mean_absolute_error: 0.3659 - val

Epoch 65/5000
117/117 [==============================] - 0s 521us/sample - loss: 0.2528 - mean_absolute_error: 0.2528 - mean_absolute_percentage_error: 74.6574 - val_loss: 0.3824 - val_mean_absolute_error: 0.3824 - val_mean_absolute_percentage_error: 167.0290
Epoch 66/5000
117/117 [==============================] - 0s 684us/sample - loss: 0.2638 - mean_absolute_error: 0.2638 - mean_absolute_percentage_error: 72.7102 - val_loss: 0.3831 - val_mean_absolute_error: 0.3831 - val_mean_absolute_percentage_error: 163.1460
Epoch 67/5000
117/117 [==============================] - 0s 462us/sample - loss: 0.2492 - mean_absolute_error: 0.2492 - mean_absolute_percentage_error: 71.5794 - val_loss: 0.3831 - val_mean_absolute_error: 0.3831 - val_mean_absolute_percentage_error: 159.4938
Epoch 68/5000
117/117 [==============================] - 0s 530us/sample - loss: 0.2671 - mean_absolute_error: 0.2671 - mean_absolute_percentage_error: 62.7822 - val_loss: 0.3823 - val_mean_absolute_error: 0.3823 - val_m

Epoch 97/5000
117/117 [==============================] - 0s 479us/sample - loss: 0.2569 - mean_absolute_error: 0.2569 - mean_absolute_percentage_error: 74.6511 - val_loss: 0.3734 - val_mean_absolute_error: 0.3734 - val_mean_absolute_percentage_error: 159.1362
Epoch 98/5000
117/117 [==============================] - 0s 462us/sample - loss: 0.2310 - mean_absolute_error: 0.2310 - mean_absolute_percentage_error: 77.8031 - val_loss: 0.3712 - val_mean_absolute_error: 0.3712 - val_mean_absolute_percentage_error: 161.3406
Epoch 99/5000
117/117 [==============================] - 0s 496us/sample - loss: 0.2144 - mean_absolute_error: 0.2144 - mean_absolute_percentage_error: 69.1457 - val_loss: 0.3684 - val_mean_absolute_error: 0.3684 - val_mean_absolute_percentage_error: 163.6970
Epoch 100/5000
117/117 [==============================] - 0s 641us/sample - loss: 0.2029 - mean_absolute_error: 0.2029 - mean_absolute_percentage_error: 76.2181 - val_loss: 0.3656 - val_mean_absolute_error: 0.3656 - val_

...

117/117 [==============================] - 0s 2ms/sample - loss: 0.1062 - mean_absolute_error: 0.1062 - mean_absolute_percentage_error: 33.2513 - val_loss: 0.3132 - val_mean_absolute_error: 0.3132 - val_mean_absolute_percentage_error: 209.9172
Epoch 3594/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.1134 - mean_absolute_error: 0.1134 - mean_absolute_percentage_error: 25.8488 - val_loss: 0.3128 - val_mean_absolute_error: 0.3128 - val_mean_absolute_percentage_error: 209.7048
Epoch 3595/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.0931 - mean_absolute_error: 0.0931 - mean_absolute_percentage_error: 25.8943 - val_loss: 0.3124 - val_mean_absolute_error: 0.3124 - val_mean_absolute_percentage_error: 209.4472
Epoch 3596/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.1226 - mean_absolute_error: 0.1226 - mean_absolute_percentage_error: 28.8073 - val_loss: 0.3120 - val_mean_absolute_error: 0.3120 - val_mean_absolute_per

117/117 [==============================] - 0s 2ms/sample - loss: 0.1204 - mean_absolute_error: 0.1204 - mean_absolute_percentage_error: 42.9804 - val_loss: 0.3134 - val_mean_absolute_error: 0.3134 - val_mean_absolute_percentage_error: 213.7448
Epoch 3656/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.1206 - mean_absolute_error: 0.1206 - mean_absolute_percentage_error: 39.2795 - val_loss: 0.3134 - val_mean_absolute_error: 0.3134 - val_mean_absolute_percentage_error: 213.6648
Epoch 3657/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.1006 - mean_absolute_error: 0.1006 - mean_absolute_percentage_error: 26.9507 - val_loss: 0.3135 - val_mean_absolute_error: 0.3135 - val_mean_absolute_percentage_error: 213.5554
Epoch 3658/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.1139 - mean_absolute_error: 0.1139 - mean_absolute_percentage_error: 35.3702 - val_loss: 0.3133 - val_mean_absolute_error: 0.3133 - val_mean_absolute_per

117/117 [==============================] - 0s 3ms/sample - loss: 0.1181 - mean_absolute_error: 0.1181 - mean_absolute_percentage_error: 37.0258 - val_loss: 0.3027 - val_mean_absolute_error: 0.3027 - val_mean_absolute_percentage_error: 204.6650
Epoch 3718/5000
117/117 [==============================] - 0s 1ms/sample - loss: 0.1026 - mean_absolute_error: 0.1026 - mean_absolute_percentage_error: 32.1821 - val_loss: 0.3028 - val_mean_absolute_error: 0.3028 - val_mean_absolute_percentage_error: 204.1128
Epoch 3719/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.0958 - mean_absolute_error: 0.0958 - mean_absolute_percentage_error: 31.2525 - val_loss: 0.3027 - val_mean_absolute_error: 0.3027 - val_mean_absolute_percentage_error: 203.5654
Epoch 3720/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.1169 - mean_absolute_error: 0.1169 - mean_absolute_percentage_error: 31.3638 - val_loss: 0.3027 - val_mean_absolute_error: 0.3027 - val_mean_absolute_per

117/117 [==============================] - 0s 2ms/sample - loss: 0.1162 - mean_absolute_error: 0.1162 - mean_absolute_percentage_error: 34.1121 - val_loss: 0.3117 - val_mean_absolute_error: 0.3117 - val_mean_absolute_percentage_error: 203.4233
Epoch 3780/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.0961 - mean_absolute_error: 0.0961 - mean_absolute_percentage_error: 31.0732 - val_loss: 0.3120 - val_mean_absolute_error: 0.3120 - val_mean_absolute_percentage_error: 203.3768
Epoch 3781/5000
117/117 [==============================] - 0s 1ms/sample - loss: 0.0976 - mean_absolute_error: 0.0976 - mean_absolute_percentage_error: 34.9696 - val_loss: 0.3119 - val_mean_absolute_error: 0.3119 - val_mean_absolute_percentage_error: 203.1481
Epoch 3782/5000
117/117 [==============================] - 0s 906us/sample - loss: 0.1017 - mean_absolute_error: 0.1017 - mean_absolute_percentage_error: 36.3808 - val_loss: 0.3117 - val_mean_absolute_error: 0.3117 - val_mean_absolute_p

117/117 [==============================] - 0s 1ms/sample - loss: 0.1187 - mean_absolute_error: 0.1187 - mean_absolute_percentage_error: 36.0303 - val_loss: 0.3090 - val_mean_absolute_error: 0.3090 - val_mean_absolute_percentage_error: 204.5353
Epoch 3842/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.1177 - mean_absolute_error: 0.1177 - mean_absolute_percentage_error: 38.0356 - val_loss: 0.3088 - val_mean_absolute_error: 0.3088 - val_mean_absolute_percentage_error: 204.2246
Epoch 3843/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.1152 - mean_absolute_error: 0.1152 - mean_absolute_percentage_error: 47.8716 - val_loss: 0.3086 - val_mean_absolute_error: 0.3086 - val_mean_absolute_percentage_error: 203.8298
Epoch 3844/5000
117/117 [==============================] - 0s 2ms/sample - loss: 0.0943 - mean_absolute_error: 0.0943 - mean_absolute_percentage_error: 27.3450 - val_loss: 0.3083 - val_mean_absolute_error: 0.3083 - val_mean_absolute_per

In [11]:
#save as excel
#===============

# Define column names for the Excel file
columns = ['Counter', 'lr', 'bs', 'MAE', 'val MAE']
# Convert Results array to a DataFrame
Results_df = pd.DataFrame(Results, columns=columns)
writer = pd.ExcelWriter(path_data_2 + "Results_file_" + str(number_of_test) + ".xlsx", engine='xlsxwriter')
Results_df.to_excel(writer, sheet_name='Results_file_', index=False)
writer.save()

In [12]:
Results_df.head(20)

Counter      lr    bs       MAE   val MAE
0         0  0.0100  1000  0.079798  0.322050
1         1  0.0010  1000  0.079198  0.261659
2         2  0.0001  1000  0.198941  0.331330
3         3  0.0100   100  0.117100  0.301322
4         4  0.0010   100  0.103972  0.283983
5         5  0.0001   100  0.123411  0.264533
6         6  0.0100    50  0.105498  0.339531
7         7  0.0010    50  0.077167  0.287679
8         8  0.0001    50  0.142959  0.297281
9         9  0.0100    20  0.117002  0.317036
10       10  0.0010    20  0.105265  0.332689
11       11  0.0001    20  0.110582  0.307864